In [2]:
import requests
import pandas as pd 
import json
import concurrent.futures
import re
import queue
import os
from bs4 import BeautifulSoup
import lxml

from collections import defaultdict
import unicodedata

In [3]:
__name = pd.read_csv("allocate_v3/VĂN HỌC.csv")
__name.columns

Index(['tên sách', 'ảnh bìa', 'thể loại', 'tác giả', 'nội dung tóm tắt',
       'giá bìa', 'nhà phát hành', 'nhà xuất bản', 'ngày xuất bản',
       'kích thước', 'loại bìa', 'số trang', 'dịch giả', 'path', 'phiên bản',
       'thương hiệu', 'xuất xứ', 'xuất xứ thương hiệu', ' isbn', 'khối lượng',
       'mã sản phẩm', 'ngày phát hành', 'ngôn ngữ', 'người dịch', 'định dạng'],
      dtype='object')

In [4]:
df2 = pd.read_csv("DATA_v2.csv")
df2.dropna(inplace = True) 
df2.columns = ["Thể loại", "Nguồn nhập", "type"]

# Remove all row that not have fahasa
df2 = df2[df2['Nguồn nhập'].str.contains("phuongnam")]
group_f1 = df2.groupby("Thể loại")["Nguồn nhập"].apply(list).to_dict()
group_f2 = df2.groupby("type")["Thể loại"].apply(list).to_dict()

n_dict = defaultdict(dict)
for k, v in group_f2.items():
    for stype in v:
        if (len(group_f1[stype])) == 1:
            _url = group_f1[stype][0].split(".html")[0]+"-page-{}.html?items_per_page=128&result_ids=pagination_contents&is_ajax=1"
            
            n_dict[k][stype] = _url
        else:
            for _ in group_f1[stype]:
                _url = _.split(".html")[0]+"-page-{}.html?items_per_page=128&result_ids=pagination_contents&is_ajax=1"
                n_dict[k][stype] = _url


In [13]:
n_dict

defaultdict(dict,
            {'CHĂM SÓC GIA ĐÌNH': {'Hạnh phúc gia đình': 'https://nhasachphuongnam.com/vi/hanh-phuc-gia-dinh-page-{}.html?items_per_page=128&result_ids=pagination_contents&is_ajax=1',
              'Cẩm nang làm cha mẹ': 'https://nhasachphuongnam.com/vi/nuoi-day-con-page-{}.html?items_per_page=128&result_ids=pagination_contents&is_ajax=1',
              'Sức khỏe dinh dưỡng cho trẻ': 'https://nhasachphuongnam.com/vi/ba-me-em-be-page-{}.html?items_per_page=128&result_ids=pagination_contents&is_ajax=1'},
             'HỌC NGÔN NGỮ': {'Sách Tiếng Anh tổng hợp': 'https://nhasachphuongnam.com/vi/tieng-anh-giao-trinh-page-{}.html?items_per_page=128&result_ids=pagination_contents&is_ajax=1',
              'Tiếng Trung': 'https://nhasachphuongnam.com/vi/tieng-hoa-1-page-{}.html?items_per_page=128&result_ids=pagination_contents&is_ajax=1',
              'Tiếng Pháp ': 'https://nhasachphuongnam.com/vi/tieng-phap-1-page-{}.html?items_per_page=128&result_ids=pagination_contents&i

In [5]:
headers = {
  'Connection': 'keep-alive',
  'Pragma': 'no-cache',
  'Cache-Control': 'no-cache',
  'sec-ch-ua': '"Chromium";v="94", "Google Chrome";v="94", ";Not A Brand";v="99"',
  'Accept': 'application/json, text/javascript, */*; q=0.01',
  'X-Requested-With': 'XMLHttpRequest',
  'sec-ch-ua-mobile': '?0',
  'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/94.0.4606.71 Safari/537.36',
  'sec-ch-ua-platform': '"Windows"',
  'Sec-Fetch-Site': 'same-origin',
  'Sec-Fetch-Mode': 'cors',
  'Sec-Fetch-Dest': 'empty',
  'Accept-Language': 'vi,en-US;q=0.9,en;q=0.8,vi-VN;q=0.7',
  'Cookie': 'sid_customer_d577e=c81a4f54e12eb374c53db1cf4d78f94e-C'
}

In [8]:
response.keys()

dict_keys(['current_url', 'html', 'notifications'])

In [12]:
html = BeautifulSoup(response['html']['pagination_contents'])

In [24]:
book_html=  html.find('div',{'class':'grid-list vs-grid-table-wrapper et-grid-table-wrapper'})
bookshelf = book_html.findAll('div',{'class':'vs-grid vs-grid-table et-grid'})
bookshelf[0].a['href']

'https://nhasachphuongnam.com/vi/bai-tap-tieng-anh-theo-chuong-trinh-moi-cua-bo-gddt-lop-9-tap-2-co-dap-an.html'

In [46]:
# infor = 'https://nhasachphuongnam.com/vi/hoang-tu-va-em-tai-ban-lan-2.html'
infor = 'https://nhasachphuongnam.com/vi/yen-lam.html'

response = requests.request("GET", infor, headers=headers, verify=False)

C:\Users\Watch Dogs\Anaconda3\envs\books\lib\site-packages\urllib3\connectionpool.py:1020: InsecureRequestWarning: Unverified HTTPS request is being made to host 'nhasachphuongnam.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  InsecureRequestWarning,


In [47]:
soup = BeautifulSoup(response.text,'html.parser')

In [28]:
soup.find('a',{'class':'cm-image-previewer cm-previewer ty-previewer'})['href']

'https://nhasachphuongnam.com/images/thumbnails/1165/1165/detailed/171/hoang_tu_va_em_tb_2.jpg'

In [29]:
soup.find('div',{'class':'product-note indented et-short-descr-wrapper'}).findChildren()[-1].text

'  Lân cười, môi anh đặt trên vành tai cô. "Anh yêu em, chỉ một mình em. Em có nghi ngờ anh không?" Ơtec lại một lần nữa đỏ mặt.   \n  ... Lân nhìn cô ngắm chiếc nhẫn, không chờ được, anh cầm lấy nó từ tay cô, nghiêng lại để cô nhìn thấy dòng chữ khắc bên trong.   \n  Không phải My heart will go...'

In [49]:
_dict = {}

features = soup.findAll('div',{'class':'ty-product-feature'})
for i in features[2:5]:
    _ = i.text.split(':')
    _dict[_[0]] = _[1]
_dict    
# soup.findAll('div',{'class':'ty-product-feature'})[3].text

{' Kích thước': ' 12.7 x 18.8 cm ',
 ' Số trang': ' 254 ',
 ' Tác giả': ' Thư Hoài '}

In [ ]:
ty-product-feature

In [38]:
soup.find('div',{'id':'content_features'}).findChildren()[21].text

'NXB Trẻ'

In [6]:
_big_dict = {}
booksQueue = queue.Queue()

class _phuongnam_Crawler():
    def __init__(self, url,category):
        self.url = url
        self.category = category
        
    def crawl(self):
        _concurrent = self._bookshelf()
        
        with concurrent.futures.ThreadPoolExecutor(max_workers=20) as executor:
            executor.map(self._books, _concurrent)
    
    def _books(self, book_url):
        
        book = {}
        
        _res = requests.request("GET", book_url, headers=headers, verify=False)
        soup = BeautifulSoup(_res.text,'html.parser')
        
        book['tên sách'] = soup.find('h1',{'class':'ty-mainbox-title'}).text
        book['ảnh bìa'] = soup.find('a',{'class':'cm-image-previewer cm-previewer ty-previewer'})['href']
        book['thể loại'] = self.category
        book['nội dung tóm tắt'] = soup.find('div',{'id':'content_description'}).text
        
        features = soup.findAll('div',{'class':'ty-product-feature'})
        for _ in features[2:5]:
            _info = _.text.split(':')
            _big_dict[_info[0]] = ''
            
            book[_info[0]] = _info[1]
            book[_info[0]] = _info[1]
            book[_info[0]] = _info[1]
        book['giá bìa'] = soup.find('span',{'class':'ty-price-num'}).text
        
        print(book)
        
        booksQueue.put(book)
            
        print(f"Number of products in my pocket {booksQueue.qsize()}")
        
    def _bookshelf(self):
        _bookshelf = []
        
        pages=0
        while True:
            print(f"Crawling pages {pages} of {self.category}")
            response = requests.request("GET", self.url.format(pages), headers=headers, verify=False).json()

            if 'html' in response.keys():
                html = BeautifulSoup(response['html']['pagination_contents'])
                book_html=  html.find('div',{'class':'grid-list vs-grid-table-wrapper et-grid-table-wrapper'})
                books = book_html.findAll('div',{'class':'vs-grid vs-grid-table et-grid'})

                for  _ in books:
                    _bookshelf.append(_.a['href'])
            else:
                break
                
            pages +=1
        return _bookshelf

In [64]:
total = 0 
rename_dict = defaultdict()

for _name in n_dict.keys():
    booksQueue = queue.Queue()
    for k,v in n_dict[_name].items():
        print(v)
        t = _phuongnam_Crawler(v, k)
        t.crawl()
        
    for i in sorted(_big_dict.keys()):
        rename_dict[i] = i.lstrip().lower()

    total += booksQueue.qsize()
    df = pd.DataFrame()
    while not booksQueue.empty():
        df = df.append(booksQueue.get(),ignore_index=True)
        df.rename(columns=rename_dict ,inplace=True)
    df.to_csv('phuongnam/phuongnam_'+ _name+'.csv',index=False)
print(f"total : {total}"")


https://nhasachphuongnam.com/vi/hanh-phuc-gia-dinh-page-{}.html?items_per_page=128&result_ids=pagination_contents&is_ajax=1
Crawling pages 0 of Hạnh phúc gia đình


C:\Users\Watch Dogs\Anaconda3\envs\books\lib\site-packages\urllib3\connectionpool.py:1020: InsecureRequestWarning: Unverified HTTPS request is being made to host 'nhasachphuongnam.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  InsecureRequestWarning,


Crawling pages 1 of Hạnh phúc gia đình


C:\Users\Watch Dogs\Anaconda3\envs\books\lib\site-packages\urllib3\connectionpool.py:1020: InsecureRequestWarning: Unverified HTTPS request is being made to host 'nhasachphuongnam.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  InsecureRequestWarning,


Crawling pages 2 of Hạnh phúc gia đình


...

{'tên sách': 'Thế Giới Xô Lệch', 'ảnh bìa': 'https://nhasachphuongnam.com/images/thumbnails/782/782/detailed/175/12676723204b8f250054585.jpg', 'thể loại': 'Văn học đương đại', 'nội dung tóm tắt': ' Tấm ảnh gia đình trong ngày cưới đối với tôi trở thành một điều gì đó thật quý giá. Trong luồng sáng chiếu rọi đâu đó từ ký ước, từ những cuộc gặp gỡ rồi chia lìa, từ khổ đau và hạnh phúc, từ những mất còn, không chỉ là của riêng tôi, nó cũng đặc biệt không kém sự kiện đêm tân hôn của đời tôi.Tôi lại đem gương mặt và cuộc đời của ba tôi, má tôi, chị tôi, anh tôi, chị dâu tôi, cháu tôi, cô tôi và chú tôi; đặt gần rồi đặt xa cùng với những hình ảnh ông tôi còn sót lại trong trí nhớ, và của bà tôi nữa, người tôi chỉ biết qua lời kể của má. Tôi lờ mờ nhận ra, trước mặt, rồi sau lưng của mỗi người là khoảng trống và giữa các thành viên của đại gia đình, cũng là khoảng trống.Khoảng trống vô hình đó hình như là nơi trú ngụ của bóng tối. Tối và thật nhiều gió.Thấy lạnh, tôi kéo mền lên tới cằm.Khoản

C:\Users\Watch Dogs\Anaconda3\envs\books\lib\site-packages\urllib3\connectionpool.py:1020: InsecureRequestWarning: Unverified HTTPS request is being made to host 'nhasachphuongnam.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  InsecureRequestWarning,
C:\Users\Watch Dogs\Anaconda3\envs\books\lib\site-packages\urllib3\connectionpool.py:1020: InsecureRequestWarning: Unverified HTTPS request is being made to host 'nhasachphuongnam.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  InsecureRequestWarning,


{'tên sách': '…Đi Ngang Đường', 'ảnh bìa': 'https://nhasachphuongnam.com/images/thumbnails/735/735/detailed/175/12729583384bdfcd828d591.jpg', 'thể loại': 'Văn học đương đại', 'nội dung tóm tắt': ' \ufeffNhiều lần bạn đọc và bà con xóm hẻm đã hỏi nhà báo tôi rằng: "Khi có những luồng thông tin khác nhau, cũng từ các cơ quan chức năng đưa ra, thì nhà báo nên chọn luồng nào để thông tin?". Phải suy nghĩ, Dân thường trả lời: "Chọn lẽ phải, chọn điều đúng và có ích cho sự phát triển đất nước, cho lợi ích của nhân dân". Trả lời như vậy nhưng người làm báo hiểu rằng không dễ dàng gì có đủ bản lĩnh để đứng về phía lẽ phải và có đủ trình độ để biết được đúng sai. Có những lúc hiệu quả được xem xét bằng lợi ích trước mắt vì tình thế, nhưng cũng có cái cho sự lâu dài bền vững của dân tộc, của nhân dân. Khi ấy, cái đúng không chỉ là nguyên lý duy nhất để chọn mà người làm báo buộc phải chọn lựa giữa cái hữu hạn của sự kiện và nỗi mong muốn vô hạn của thông tin. Lúc đó nhà báo phải biết vị trí của 

C:\Users\Watch Dogs\Anaconda3\envs\books\lib\site-packages\urllib3\connectionpool.py:1020: InsecureRequestWarning: Unverified HTTPS request is being made to host 'nhasachphuongnam.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  InsecureRequestWarning,


{'tên sách': 'Linh Miêu Ba Sắc', 'ảnh bìa': 'https://nhasachphuongnam.com/images/thumbnails/790/790/detailed/175/12772625894c217afdaf90c.jpg', 'thể loại': 'Văn học đương đại', 'nội dung tóm tắt': ' \ufeffTrong phần đông chúng ta, ít nhiều gì chắc cũng đã được nghe người xưa nhắc nhở: "Hễ trong nhà có người thân chết, thì tuyệt đối không cho loài Mèo đến gần xác khi chưa được tẩm liệm".Bởi theo họ, trong dòng họ nhà Mèo có một loại rất nguy hiểm. Loại này nó mang trên người 3 sắc lông nằm cuộn tròn ở phần đuôi, mà người đời thường gọi là "Linh Miêu Ba Sắc".Theo kinh nghiệm, người xưa nói rằng: "Nếu để loài Mèo này cố hay vô tình phóng ngang xác chết thì hiện tượng ma quỷ sẽ xuất hiện ở từng góc độ và hoàn cảnh khác nhau! Lúc đó thân thể người chết sẽ bật dậy và đuổi bắt bất kỳ ai ở gần nhất". Có người nói, hễ nó chạm vào ai khác thì người đó sẽ chết theo... ', ' Kích thước': ' 13.5x20.5x0.8 cm ', ' Số trang': ' 178 ', ' Tác giả': ' Cao Bồi Vườn Phương Bằng ', 'giá bìa': '14,000'}
Number

In [10]:
n_dict

defaultdict(dict,
            {'CHĂM SÓC GIA ĐÌNH': {'Hạnh phúc gia đình': 'https://nhasachphuongnam.com/vi/hanh-phuc-gia-dinh-page-{}.html?items_per_page=128&result_ids=pagination_contents&is_ajax=1',
              'Cẩm nang làm cha mẹ': 'https://nhasachphuongnam.com/vi/nuoi-day-con-page-{}.html?items_per_page=128&result_ids=pagination_contents&is_ajax=1',
              'Sức khỏe dinh dưỡng cho trẻ': 'https://nhasachphuongnam.com/vi/ba-me-em-be-page-{}.html?items_per_page=128&result_ids=pagination_contents&is_ajax=1'},
             'HỌC NGÔN NGỮ': {'Sách Tiếng Anh tổng hợp': 'https://nhasachphuongnam.com/vi/tieng-anh-giao-trinh-page-{}.html?items_per_page=128&result_ids=pagination_contents&is_ajax=1',
              'Tiếng Trung': 'https://nhasachphuongnam.com/vi/tieng-hoa-1-page-{}.html?items_per_page=128&result_ids=pagination_contents&is_ajax=1',
              'Tiếng Pháp ': 'https://nhasachphuongnam.com/vi/tieng-phap-1-page-{}.html?items_per_page=128&result_ids=pagination_contents&i

In [16]:
for _name in n_dict.keys():
    booksQueue = queue.Queue()
#     print(n_dict[_name])
#     print(len(n_dict[_name]))
    for k,v in n_dict[_name].items():
        print(k,v)

Hạnh phúc gia đình https://nhasachphuongnam.com/vi/hanh-phuc-gia-dinh-page-{}.html?items_per_page=128&result_ids=pagination_contents&is_ajax=1
Cẩm nang làm cha mẹ https://nhasachphuongnam.com/vi/nuoi-day-con-page-{}.html?items_per_page=128&result_ids=pagination_contents&is_ajax=1
Sức khỏe dinh dưỡng cho trẻ https://nhasachphuongnam.com/vi/ba-me-em-be-page-{}.html?items_per_page=128&result_ids=pagination_contents&is_ajax=1
Sách Tiếng Anh tổng hợp https://nhasachphuongnam.com/vi/tieng-anh-giao-trinh-page-{}.html?items_per_page=128&result_ids=pagination_contents&is_ajax=1
Tiếng Trung https://nhasachphuongnam.com/vi/tieng-hoa-1-page-{}.html?items_per_page=128&result_ids=pagination_contents&is_ajax=1
Tiếng Pháp  https://nhasachphuongnam.com/vi/tieng-phap-1-page-{}.html?items_per_page=128&result_ids=pagination_contents&is_ajax=1
Tiếng Hàn  https://nhasachphuongnam.com/vi/tieng-han-page-{}.html?items_per_page=128&result_ids=pagination_contents&is_ajax=1
Tiếng Nhật  https://nhasachphuongnam.co

In [35]:
t = _phuongnam_Crawler('https://nhasachphuongnam.com/vi/hanh-phuc-gia-dinh-page-{}.html?items_per_page=128&result_ids=pagination_contents&is_ajax=1','Hạnh phúc gia đình')
print(t._bookshelf())
t._books('https://nhasachphuongnam.com/vi/trach-nhiem-gia-dinh-la-huu-han.html')

Crawling pages 0 of Hạnh phúc gia đình


C:\Users\Watch Dogs\Anaconda3\envs\books\lib\site-packages\urllib3\connectionpool.py:1020: InsecureRequestWarning: Unverified HTTPS request is being made to host 'nhasachphuongnam.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  InsecureRequestWarning,


Crawling pages 1 of Hạnh phúc gia đình


C:\Users\Watch Dogs\Anaconda3\envs\books\lib\site-packages\urllib3\connectionpool.py:1020: InsecureRequestWarning: Unverified HTTPS request is being made to host 'nhasachphuongnam.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  InsecureRequestWarning,


Crawling pages 2 of Hạnh phúc gia đình
['https://nhasachphuongnam.com/vi/trach-nhiem-gia-dinh-la-huu-han.html', 'https://nhasachphuongnam.com/vi/hon-nhan-doc-ban-hanh-trinh-co-1-0-2.html', 'https://nhasachphuongnam.com/vi/lan-dau-lam-ong-ba.html', 'https://nhasachphuongnam.com/vi/nguoi-vo-biet-uoc-mo-se-tre-mai-khong-gia.html', 'https://nhasachphuongnam.com/vi/thi-tham-chuyen-nho-chuyen-to.html', 'https://nhasachphuongnam.com/vi/co-con-va-van-son-cha-me-gianh-lai-cuoc-song-rieng-tu.html', 'https://nhasachphuongnam.com/vi/sau-loi-the-uoc-du-cho-mua-nang-van-thuong-nhau.html', 'https://nhasachphuongnam.com/vi/so-tay-ke-hoach-cuoi-de-to-chuc-dam-cuoi-trong-mo-cua-ban.html', 'https://nhasachphuongnam.com/vi/cuoi-di-doi-chi.html', 'https://nhasachphuongnam.com/vi/5-ngon-ngu-yeu-thuong.html', 'https://nhasachphuongnam.com/vi/vo-chong-va-nguoi-thu-ba.html', 'https://nhasachphuongnam.com/vi/anh-la-chu-re-em-la-co-dau-moi-dieu-ban-can-biet-de-co-mot-dam-cuoi-tuyet-voi.html', 'https://nhasachphu

C:\Users\Watch Dogs\Anaconda3\envs\books\lib\site-packages\urllib3\connectionpool.py:1020: InsecureRequestWarning: Unverified HTTPS request is being made to host 'nhasachphuongnam.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  InsecureRequestWarning,
C:\Users\Watch Dogs\Anaconda3\envs\books\lib\site-packages\urllib3\connectionpool.py:1020: InsecureRequestWarning: Unverified HTTPS request is being made to host 'nhasachphuongnam.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  InsecureRequestWarning,


{'tên sách': 'Trách Nhiệm Gia Đình Là Hữu Hạn', 'ảnh bìa': 'https://nhasachphuongnam.com/images/thumbnails/900/900/detailed/220/trach-nhiem-gia-dinh-la-huu-han.jpg', 'thể loại': 'Hạnh phúc gia đình', 'nội dung tóm tắt': '  Trách nhiệm gia đình là hữu hạn đào sâu tìm hiểu về cốt lõi của mối quan hệ mẹ con, đồng thời tiết lộ những tác động có thể xảy ra do hành vi của cha mẹ đối với cuộc sống về sau của con cái. Cuốn sách cũng chỉ ra cách chúng ta nên nhận thức và thay đổi tư duy để giải quyết những vấn đề đang tồn tại của chính mình. Nội dung được chia thành sáu phần, bao gồm những vấn đề hoặc rõ ràng, hoặc tiềm ẩn trong gia đình, từ các khía cạnh của mối quan hệ mẹ con, giáo dục gia đình và nhận thức về bản thân. “Tình yêu thương và sự tự do” là quan niệm giáo dục gia đình nhất quán của tác giả được thể hiện xuyên suốt trong cuốn sách. Điều này cũng được phản ánh qua ý thức về ranh giới trong các mối quan hệ. Cho dù đối với trẻ em hay đối với chính bạn, giữ ranh giới là một yếu tố quan

In [2]:
_df = pd.read_csv("phuongnam/phuongnam_CHĂM SÓC GIA ĐÌNH.csv")
_df.head()

tên sách  \
0                       Keep Calm - Bình Thản Làm Mẹ   
1  Anh Là Chú Rể, Em Là Cô Dâu - Mọi Điều Bạn Cần...   
2              Combo Gia Đình Yêu Thương (Bộ 3 Cuốn)   
3  Sau Lời Thề Ước - Dù Cho Mưa Nắng Vẫn Thương Nhau   
4  Có Con Và Vẫn Son - Cha Mẹ Giành Lại Cuộc Sống...   

                                             ảnh bìa            thể loại  \
0  https://nhasachphuongnam.com/images/thumbnails...  Hạnh phúc gia đình   
1  https://nhasachphuongnam.com/images/thumbnails...  Hạnh phúc gia đình   
2  https://nhasachphuongnam.com/images/thumbnails...  Hạnh phúc gia đình   
3  https://nhasachphuongnam.com/images/thumbnails...  Hạnh phúc gia đình   
4  https://nhasachphuongnam.com/images/thumbnails...  Hạnh phúc gia đình   

                                    nội dung tóm tắt  số trang  \
0   Keep Calm - Bình Thản Làm Mẹ "Người mẹ vất vả...     160.0   
1    Mỗi ngày và mỗi ngày, biết bao đôi tình nhân...     342.0   
2   Combo Gia Đình Yêu Thương (Bộ 3 Cuốn) "Bộ sác...       NaN   
3    Chúng ta vẫn thường nói vui với nhau rằng: “...     160.0   
4    Cuốn sách nói về cách các bậc cha mẹ hiện đạ...     383.0   

             tác giả    dịch giả  giá bìa      kích thước nhà phát hành  \
0       Pauline Loh    Thái Hòa    65,000             NaN           NaN   
1           Như Cầm          NaN  270,000   15.5 x 24 cm            NaN   
2                NaN         NaN  242,000             NaN   First News    
3       P. J. Larue          NaN   69,000     13 x 19 cm            NaN   
4   Rachel Bertsche          NaN  145,000   13 x 20.5 cm            NaN   

                                  nhà xuất bản  
0                                          NaN  
1                                          NaN  
2   NXB Tổng hợp TP.HCMNXB Văn Hóa - Văn Nghệ   
3                                          NaN  
4                                          NaN

In [39]:
a = booksQueue.get()

In [54]:
rename_dict = defaultdict()
for i in sorted(a.keys()):
#     print(unicodedata.normalize("NFKD",i))
    print(i.lstrip().lower())
#     word1 = " ".join(re.findall("[^a-z0-9A-Z_ÀÁÂÃÈÉÊÌÍÒÓÔÕÙÚĂĐĨŨƠàáâãèéêìíòóôõùúăđĩũơƯĂẠẢẤẦẨẪẬẮẰẲẴẶẸẺẼỀỀỂưăạảấầẩẫậắằẳẵặẹẻẽềềểỄỆỈỊỌỎỐỒỔỖỘỚỜỞỠỢỤỦỨỪễệỉịọỏốồổỗộớờởỡợụủứừỬỮỰỲỴÝỶỸửữựỳỵỷỹ]+", i))
#     rename_dict[i] = i[1:]
#     rename_dict['định dạng'] = 'loại bìa'
#     rename_dict['ngày phát hành'] ='ngày xuất bản'
#     rename_dict['người dịch'] = 'dịch giả'


kích thước
số trang
tác giả
giá bìa
nội dung tóm tắt
thể loại
tên sách
ảnh bìa
